In [1]:
#!wget http://opus.nlpl.eu/download.php?f=OpenSubtitles/v2018/mono/OpenSubtitles.raw.en.gz

In [2]:
#import os
#!gunzip -c download.php?f=OpenSubtitles%2Fv2018%2Fmono%2FOpenSubtitles.raw.en.gz >/tmp/lines

In [3]:
##os.mkdir ('/tmp/lines')
#!split -a 3 -l 100000 download.php?f=OpenSubtitles%2Fv2018%2Fmono%2FOpenSubtitles.raw.en.gz /tmp/lines-

In [4]:
##BUCKET="your-bucket"
##gsutil -m cp -r lines gs://${BUCKET?}/opensubtitles/raw/""

In [5]:
! wget https://object.pouta.csc.fi/OPUS-OpenSubtitles/v2018/mono/en.txt.gz

--2020-06-25 15:08:57--  https://object.pouta.csc.fi/OPUS-OpenSubtitles/v2018/mono/en.txt.gz
Resolving object.pouta.csc.fi (object.pouta.csc.fi)... 86.50.254.18, 86.50.254.19
Connecting to object.pouta.csc.fi (object.pouta.csc.fi)|86.50.254.18|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 3663376519 (3.4G) [application/gzip]
Saving to: ‘en.txt.gz’

en.txt.gz           100%[===================>]   3.41G  21.4MB/s    in 2m 47s  

2020-06-25 15:11:45 (21.0 MB/s) - ‘en.txt.gz’ saved [3663376519/3663376519]



In [6]:
#gunzip command is used to compress or expand a file or a list of files in Linux. 
#It accepts all the files having extension as .gz, .z, _z, -gz, -z , .Z, .taz or.tgz 
#and replace the compressed file with the original file by default. 
#The files after uncompression retain its actual extension.
! apt install gunzip
! gunzip en.txt.gz

Reading package lists... Done
Building dependency tree       
Reading state information... Done
E: Unable to locate package gunzip


In [7]:
#The tail command, as the name implies, print the last N number of data of the given input. 
#By default it prints the last 10 lines of the specified files. 
# can refer to:  geeksforgeeks.org/tail-command-linux-examples/

!tail en.txt

- No, no, no, no!
- You killed my friend, my best friend, my lifelong friend!
I'm gonna kill every one of you!
- Get out of here!
Watch out!
No!
Oh, I've never been so glad to see anybody in my life.
What happened to him?
- He bled to death.
Come on, let's get the hell out of here.


In [8]:
!tail -7 en.txt

- Get out of here!
Watch out!
No!
Oh, I've never been so glad to see anybody in my life.
What happened to him?
- He bled to death.
Come on, let's get the hell out of here.


In [9]:
#! split -a 3 -l 100000 en.txt lines/lines-
! split -a 3 -l 100000 --verbose en.txt /tmp/lines-

creating file '/tmp/lines-aaa'
creating file '/tmp/lines-aab'
creating file '/tmp/lines-aac'
creating file '/tmp/lines-aad'
creating file '/tmp/lines-aae'
creating file '/tmp/lines-aaf'
creating file '/tmp/lines-aag'
creating file '/tmp/lines-aah'
creating file '/tmp/lines-aai'
creating file '/tmp/lines-aaj'
creating file '/tmp/lines-aak'
creating file '/tmp/lines-aal'
creating file '/tmp/lines-aam'
creating file '/tmp/lines-aan'
creating file '/tmp/lines-aao'
creating file '/tmp/lines-aap'
creating file '/tmp/lines-aaq'
creating file '/tmp/lines-aar'
creating file '/tmp/lines-aas'
creating file '/tmp/lines-aat'
creating file '/tmp/lines-aau'
creating file '/tmp/lines-aav'
creating file '/tmp/lines-aaw'
creating file '/tmp/lines-aax'
creating file '/tmp/lines-aay'
creating file '/tmp/lines-aaz'
creating file '/tmp/lines-aba'
creating file '/tmp/lines-abb'
creating file '/tmp/lines-abc'
creating file '/tmp/lines-abd'
creating file '/tmp/lines-abe'
creating file '/tmp/lines-abf'
creating

In [10]:
# here line_cleaner is a function which brings all the characters to lowercase and removes some of the punctuations
def line_cleaner(line):
    line=line.lower()
    temp=""
    for char in line:
#       print(char)
        if char!= "," and char!= "!" and char!= "?" and char!= "." and char!= "-":
         if char!=',':
            temp+=char
    return temp

#example
line_cleaner("Where are you going? I am thinking of returning to the campus, but I- CANNOT!")

'where are you going i am thinking of returning to the campus but i cannot'

In [11]:
import re

def _should_skip(line, min_length, max_length):
    """Whether a line should be skipped depending on the length."""
    return len(line) < min_length or len(line) > max_length

In [12]:
def _preprocess_line(line):
    line = line.decode("utf-8")
    
    #The re. sub() function is used to replace occurrences of a particular sub-string with another sub-string.

    # Remove the first word if it is followed by colon (speaker names)
    # NOTE: this wont work if the speaker's name has more than one word
    
    
    line = re.sub('(?:^|(?:[.!?]\\s))(\\w+):', "", line)

    # Remove anything between brackets (corresponds to acoustic events).
    line = re.sub("[\\[(](.*?)[\\])]", "", line)

    # Strip blanks hyphens and line breaks
    line = line.strip(" -\n")

    return line

In [13]:
def create_example(previous_lines, line, file_id):
    """Creates examples with multi-line context
    The examples will include:
        file_id: the name of the file where these lines were obtained.
        response: the current line text
        context: the previous line text
        context/0: 2 lines before
        context/1: 3 lines before, etc.
    """
    example = {
        'file_id': file_id,
        'context': previous_lines[-1],
        'response': line,
    }
    example['file_id'] = file_id
    example['context'] = previous_lines[-1]

    extra_contexts = previous_lines[:-1]
    example.update({
        'context/{}'.format(i): context
        for i, context in enumerate(extra_contexts[::-1])
    })

    return example

In [14]:
def _create_examples_from_file(file_name, min_length=0, max_length=20,
                               num_extra_contexts=5):

    previous_lines = []
    with open(file_name, 'rb') as f:
      for line in f :
        line = _preprocess_line(line)
        if not line:
            continue

        should_skip = _should_skip(
            line,
            min_length=min_length,
            max_length=max_length)

        if previous_lines:
            should_skip |= _should_skip(
                previous_lines[-1],
                min_length=min_length,
                max_length=max_length)

            if not should_skip:
                yield create_example(previous_lines, line, file_name)

        previous_lines.append(line)
        if len(previous_lines) > num_extra_contexts + 1:
            del previous_lines[0]

In [15]:
example = _create_examples_from_file(file_name='/tmp/lines-gln')

count = 0
for i in example:
  count += 1
print('Found '+ str(count*5) + ' examples')
print(i)

Found 110985 examples
{'file_id': '/tmp/lines-gln', 'context': 'That was close!', 'response': 'We could have died!', 'context/0': "I can't go to sleep", 'context/1': "What's with all the noise?", 'context/2': "Hey how come this idiot didn't get hit?", 'context/3': 'What he said is true', 'context/4': 'Ha!'}


In [16]:
test = _create_examples_from_file(file_name='/tmp/lines-gln')
for x in test:
  print(x)

Streaming output truncated to the last 5000 lines.
{'file_id': '/tmp/lines-gln', 'context': 'JT', 'response': 'JT', 'context/0': "I got issues I'm dealing with, too, okay?", 'context/1': 'Yeah, well, it would be nice if someone cared about my ass once in a while.', 'context/2': 'I knew this would bite me in the ass.', 'context/3': 'Get me Cat, all right?', 'context/4': 'Damn it.'}
{'file_id': '/tmp/lines-gln', 'context': 'JT', 'response': 'JT?', 'context/0': 'JT', 'context/1': "I got issues I'm dealing with, too, okay?", 'context/2': 'Yeah, well, it would be nice if someone cared about my ass once in a while.', 'context/3': 'I knew this would bite me in the ass.', 'context/4': 'Get me Cat, all right?'}
{'file_id': '/tmp/lines-gln', 'context': 'JT?', 'response': 'JT?', 'context/0': 'JT', 'context/1': 'JT', 'context/2': "I got issues I'm dealing with, too, okay?", 'context/3': 'Yeah, well, it would be nice if someone cared about my ass once in a while.', 'context/4': 'I knew this would b

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



Streaming output truncated to the last 5000 lines.
{'file_id': '/tmp/lines-gln', 'context': 'And so...', 'response': 'I killed him.', 'context/0': 'I had to take swift action.', 'context/1': 'Lives hung in the balance.', 'context/2': 'There were hybrids in the building with bombs.', 'context/3': "I don't know.", 'context/4': 'Who?'}
{'file_id': '/tmp/lines-gln', 'context': 'Dead or alive?', 'response': 'Either.', 'context/0': 'Find Molly Woods and bring her in.', 'context/1': 'Dispatch a Humanichs team.', 'context/2': 'All those missing have been accounted for, except for Molly Woods.', 'context/3': "Madam Secretary, we've identified the bodies.", 'context/4': 'I thought so.'}
{'file_id': '/tmp/lines-gln', 'context': 'Either.', 'response': "Yes, ma'am.", 'context/0': 'Dead or alive?', 'context/1': 'Find Molly Woods and bring her in.', 'context/2': 'Dispatch a Humanichs team.', 'context/3': 'All those missing have been accounted for, except for Molly Woods.', 'context/4': "Madam Secreta

In [17]:
test = _create_examples_from_file(file_name='/tmp/lines-gln')
for x in test:
  print(x['context/0'])

KeyError: ignored

In [32]:
test = _create_examples_from_file(file_name='/tmp/lines-aaa')
for x in test:
  print(x)

Streaming output truncated to the last 5000 lines.
{'file_id': '/tmp/lines-aaa', 'context': 'All right.', 'response': 'Hey, Pilgrim!', 'context/0': "I'll change, you saddle him.", 'context/1': 'Ride him!', 'context/2': "What'll you do with his horse?", 'context/3': "He didn't go bad.", 'context/4': 'I knew him as a troubleshooter in Santa Fe before he went bad.'}
{'file_id': '/tmp/lines-aaa', 'context': 'Hey, Pilgrim!', 'response': 'Come here!', 'context/0': 'All right.', 'context/1': "I'll change, you saddle him.", 'context/2': 'Ride him!', 'context/3': "What'll you do with his horse?", 'context/4': "He didn't go bad."}
{'file_id': '/tmp/lines-aaa', 'context': "You've got a bet.", 'response': 'And you got stuck.', 'context/0': "$100 aging yours I'm right.", 'context/1': "That's ridiculous.", 'context/2': "They'll get you to end of track before the train does.", 'context/3': 'On one of these?', 'context/4': "I can take you to where it's going."}
{'file_id': '/tmp/lines-aaa', 'context':

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



Streaming output truncated to the last 5000 lines.
{'file_id': '/tmp/lines-aaa', 'context': 'Use your knife, man.', 'response': 'On your feet!', 'context/0': 'Come along, Thomson.', 'context/1': 'Good show!', 'context/2': 'Good show, Jenkins.', 'context/3': "Major Warden's bungalow is at the end of the path.", 'context/4': 'Oh, yes.'}
{'file_id': '/tmp/lines-aaa', 'context': "You're sorry?", 'response': 'So am I.', 'context/0': "I'm terribly sorry, sir.", 'context/1': 'Wait a minute!', 'context/2': "You see, he's gained the initiative.", 'context/3': 'Always use your knife immediately, Joyce.', 'context/4': 'Very clumsy, Joyce, very clumsy.'}
{'file_id': '/tmp/lines-aaa', 'context': 'Yes, sir.', 'response': 'Sorry, sir.', 'context/0': "That'll be all, Joyce.", 'context/1': "I'm American, if that's what you mean.", 'context/2': 'I thought you were the enemy.', 'context/3': 'So am I.', 'context/4': "You're sorry?"}
{'file_id': '/tmp/lines-aaa', 'context': 'Major Warden, sir?', 'response'

In [33]:
test = _create_examples_from_file(file_name='/tmp/lines-aaa')
for x in test:
  print(x['context/2'])

Streaming output truncated to the last 5000 lines.
Good show, Jenkins.
You see, he's gained the initiative.
I thought you were the enemy.
That's the end of his lecture.
Thunderous ovation.
Yes?
Thanks for telling me.
Go ahead.
Oh, I'm dying for a cup of tea.
A drink?
Under the circumstances it's a bit much but you have a unique knowledge for our purpose.
When the Navy learns the truth, they'll say:
In one sense you're a hero for making an escape from the jungle.
Hot potato.
As far as your rank is concerned we're fairly informal about that in Force 316.
Oh, Colonel Green, sir.
Hello, Clipton.
He's been most reasonable since we took over.
What's he thinking?
What do you think?
Quite a challenge, isn't it?
Are you convinced that building this bridge is a good idea?
British soldiers, even in captivity.
Yes, sir.
You were in need of medical attention?
Sir?
How did you wind up here?
Well, I think that's all.
I had an air reconnaissance report on the village.
There's enough clearing to make y

In [36]:
test = _create_examples_from_file(file_name='/tmp/lines-aaa')
inputs = []
responses = []
i = 0

for t in test:

  response= t['response']
  input_1 = t['context']
  input_2 = t['context/0']
  input_3 = t['context/1']
  input_4 = t['context/2']
  input_5 = t['context/3']
  
  inputs.append(line_cleaner(input_1))
  inputs.append(line_cleaner(input_2))
  inputs.append(line_cleaner(input_3))
  inputs.append(line_cleaner(input_4))
  inputs.append(line_cleaner(input_5))
    
  for j in range(5):
    responses.append('START' + ' ' +line_cleaner(response)+ ' ' + 'END')
    
  i += 5

print(len(inputs))
print(len(responses))

101770
101770


In [39]:
print(inputs[1100], responses[1100])

what officer START keep quiet END


In [41]:
from tensorflow.keras.preprocessing.text import Tokenizer 
from tensorflow.keras.preprocessing.sequence import pad_sequences

oov_token = "<OOV>"
max_length = 25

tokenizer = Tokenizer(oov_token=oov_token)
tokenizer.fit_on_texts(inputs)
tokenizer.fit_on_texts(responses)

word_index = tokenizer.word_index
word_index['START'] = 0
word_index['END'] = len(word_index)+1
index_word = {word_index[word]:word for word in word_index}
print(index_word)

vocab_size = len(word_index) + 1
input_seq = tokenizer.texts_to_sequences(inputs)
response_seq = tokenizer.texts_to_sequences(responses)
input_seq_pad = pad_sequences(input_seq, maxlen = max_length ,padding = 'post', truncating = 'post')
response_seq_pad = pad_sequences(response_seq, maxlen = max_length, padding = 'post', truncating = 'post')

print(len(word_index))
print(inputs[0], responses[0])
print(input_seq_pad[0], response_seq_pad[0])
print(len(input_seq_pad))

{1: '<OOV>', 2: 'end', 3: 'start', 4: 'you', 5: 'i', 6: 'the', 7: 'to', 8: 'a', 9: 'it', 10: 'me', 11: 'no', 12: 'is', 13: 'what', 14: 'yes', 15: 'of', 16: 'sir', 17: 'on', 18: 'and', 19: 'in', 20: 'go', 21: 'here', 22: 'are', 23: 'that', 24: 'do', 25: 'good', 26: 'come', 27: 'not', 28: "i'm", 29: 'your', 30: 'this', 31: "it's", 32: 'gyeonwoo', 33: 'right', 34: 'for', 35: "don't", 36: 'be', 37: 'all', 38: 'him', 39: 'he', 40: 'we', 41: 'have', 42: 'up', 43: 'my', 44: 'get', 45: 'know', 46: 'see', 47: 'with', 48: 'if', 49: 'so', 50: 'why', 51: 'oh', 52: "that's", 53: 'how', 54: 'there', 55: 'was', 56: 'well', 57: 'can', 58: "he's", 59: 'will', 60: 'but', 61: 'now', 62: 'one', 63: 'about', 64: "you're", 65: 'thank', 66: "i'll", 67: 'hey', 68: 'down', 69: 'at', 70: 'just', 71: 'man', 72: 'like', 73: "what's", 74: "let's", 75: 'let', 76: 'got', 77: 'please', 78: 'going', 79: 'time', 80: 'out', 81: 'us', 82: 'they', 83: 'too', 84: 'help', 85: 'sorry', 86: 'or', 87: 'take', 88: 'her', 89: 'd

In [62]:
def preprocess(text_list):
  inputs = []
  for tmp in text_list:
    inputs.append(line_cleaner(tmp))
  input_seq = tokenizer.texts_to_sequences(inputs)
  input_seq_pad = pad_sequences(input_seq, maxlen = max_length ,padding = 'post', truncating = 'post')
  return input_seq_pad

Loading pre-trained word embeddings (GloVe embeddings)into a frozen Keras Embedding layer, and using it to
train a attention model 

Reference1 : https://blog.keras.io/using-pre-trained-word-embeddings-in-a-keras-model.html

Reference2 : https://github.com/keras-team/keras/blob/master/examples/pretrained_word_embeddings.py

GloVe embedding data can be found at : http://nlp.stanford.edu/data/glove.6B.zip
(source page: http://nlp.stanford.edu/projects/glove/)

compute an index mapping words to known embeddings, by parsing the data dump of pre-trained embeddings:
first, build index mapping words in the embeddings set to their embedding vector

In [43]:
!wget http://nlp.stanford.edu/data/glove.6B.zip
!unzip glove.6B.zip

--2020-06-25 15:51:04--  http://nlp.stanford.edu/data/glove.6B.zip
Resolving nlp.stanford.edu (nlp.stanford.edu)... 171.64.67.140
Connecting to nlp.stanford.edu (nlp.stanford.edu)|171.64.67.140|:80... connected.
HTTP request sent, awaiting response... 302 Found
Location: https://nlp.stanford.edu/data/glove.6B.zip [following]
--2020-06-25 15:51:04--  https://nlp.stanford.edu/data/glove.6B.zip
Connecting to nlp.stanford.edu (nlp.stanford.edu)|171.64.67.140|:443... connected.
HTTP request sent, awaiting response... 301 Moved Permanently
Location: http://downloads.cs.stanford.edu/nlp/data/glove.6B.zip [following]
--2020-06-25 15:51:05--  http://downloads.cs.stanford.edu/nlp/data/glove.6B.zip
Resolving downloads.cs.stanford.edu (downloads.cs.stanford.edu)... 171.64.64.22
Connecting to downloads.cs.stanford.edu (downloads.cs.stanford.edu)|171.64.64.22|:80... connected.
HTTP request sent, awaiting response... 200 OK
Length: 862182613 (822M) [application/zip]
Saving to: ‘glove.6B.zip’

glove.6

In [44]:
import numpy as np
import os

GLOVE_DIR = './'

embeddings_index = {} #initialize dictionary
f = open(os.path.join(GLOVE_DIR, 'glove.6B.100d.txt'))
for line in f:
    values = line.split()
    word = values[0]
    coefs = np.asarray(values[1:], dtype='float32')
    embeddings_index[word] = coefs
f.close()

print('Found %s word vectors.' % len(embeddings_index))

Found 400000 word vectors.


In [45]:

embedding_dim = 100
embeddings_matrix = np.zeros((vocab_size+1, embedding_dim))

for word, i in word_index.items():
    embedding_vector = embeddings_index.get(word)
    if embedding_vector is not None:
        embeddings_matrix[i] = embedding_vector

In [46]:
print(len(embeddings_matrix))
embeddings_matrix

7071


array([[0.        , 0.        , 0.        , ..., 0.        , 0.        ,
        0.        ],
       [0.        , 0.        , 0.        , ..., 0.        , 0.        ,
        0.        ],
       [0.14726   , 0.088411  , 0.28386   , ..., 0.28485999, 0.50204003,
        0.083894  ],
       ...,
       [0.        , 0.        , 0.        , ..., 0.        , 0.        ,
        0.        ],
       [0.        , 0.        , 0.        , ..., 0.        , 0.        ,
        0.        ],
       [0.        , 0.        , 0.        , ..., 0.        , 0.        ,
        0.        ]])

In [48]:

embeddings_matrix[27]

array([-1.91039994e-01,  1.76009998e-01,  3.69199991e-01, -5.03229976e-01,
       -4.75609988e-01,  1.57979995e-01, -1.16789997e-01,  2.10519999e-01,
        3.26519996e-01,  1.21940002e-01,  9.09439996e-02,  2.60890007e-01,
        7.62939990e-01,  6.96729985e-04, -5.00009991e-02, -4.48529989e-01,
        3.62390012e-01,  5.63449979e-01, -6.87020004e-01,  3.32370013e-01,
        3.12849998e-01, -1.42069995e-01,  3.53269994e-01, -1.64260000e-01,
       -1.06930003e-01,  7.77859986e-02, -1.77039996e-01, -9.28969979e-01,
        1.46799996e-01, -1.35849997e-01,  2.56819993e-01,  6.60189986e-01,
       -3.55690002e-01,  2.18380004e-01,  3.81729990e-01,  5.43370008e-01,
        1.01970002e-01,  3.52299988e-01, -2.55100012e-01, -1.51549995e-01,
       -6.74340010e-01,  1.69029996e-01,  1.64130002e-01, -5.38429976e-01,
       -1.74569994e-01, -2.85389990e-01,  7.40440011e-01, -6.75329983e-01,
       -2.33820006e-01, -1.35990000e+00,  3.02249998e-01, -1.49680004e-01,
        2.70429999e-01,  

In [49]:
print(len(input_seq_pad))
input_seq_pad

101770


array([[  28,   78,    7, ...,    0,    0,    0],
       [  40,  786,    7, ...,    0,    0,    0],
       [1020,  138,  194, ...,    0,    0,    0],
       ...,
       [ 114,   10,  448, ...,    0,    0,    0],
       [   5,   41,    0, ...,    0,    0,    0],
       [   4, 2051,    7, ...,    0,    0,    0]], dtype=int32)

In [50]:
print(len(response_seq_pad))

101770


In [51]:
X_train = []
y_train = []
for j in range(101769):
    X_train.append(input_seq_pad[j])
    y_train.append(response_seq_pad[j])

X_train = np.array(X_train)
y_train = np.array(y_train)

print(embedding_dim)
print(X_train.shape)
print(y_train.shape)

dataset = (inputs, responses)

100
(101769, 25)
(101769, 25)


In [52]:
import os
import pickle
import numpy as np
import tensorflow as tf
from tensorflow.keras.preprocessing.text import Tokenizer
from tensorflow.keras.preprocessing.sequence import pad_sequences
from tensorflow.keras.layers import Embedding, GRU, Dense 

max_sequence_len = 25
batch_size = 64
train_dataset = tf.data.Dataset.from_tensor_slices((X_train, y_train))
train_dataset = train_dataset.cache()
train_dataset = train_dataset.shuffle(1024)
train_dataset = train_dataset.batch(batch_size, drop_remainder=True)
train_dataset = train_dataset.prefetch(tf.data.experimental.AUTOTUNE)

In [53]:
class Encoder(tf.keras.Model):
    def __init__(self, hidden_size=1024, max_sequence_len=25, batch_size=batch_size, embedding_dim=100, vocab_size=vocab_size+1):
        super(Encoder, self).__init__()
        self.embedding_dim = embedding_dim
        self.vocab_size = vocab_size
        self.max_sequence_len = max_sequence_len
        self.hidden_size = hidden_size
        self.batch_size = batch_size

        self.embedding_layer = Embedding(
            input_dim=self.vocab_size, output_dim=self.embedding_dim, weights=[embeddings_matrix], trainable=False)
        self.GRU_1 = GRU(units=hidden_size, return_sequences=True,recurrent_initializer='glorot_uniform')
        self.GRU_2 = GRU(units=hidden_size,
                         return_sequences=True, return_state=True,recurrent_initializer='glorot_uniform')

    def initial_hidden_state(self):
        return tf.zeros(shape=(self.batch_size, self.hidden_size))

    def call(self, x, initial_state, training=False):
        x = self.embedding_layer(x)
        x = self.GRU_1(x, initial_state=initial_state)
        x, hidden_state = self.GRU_2(x)
        return x, hidden_state

In [54]:
class Attention(tf.keras.Model):
    def __init__(self, hidden_size=256):
        super(Attention, self).__init__()
        self.fc1 = Dense(units=hidden_size)
        self.fc2 = Dense(units=hidden_size)
        self.fc3 = Dense(units=1)

    def call(self, encoder_output, hidden_state, training=False):
        '''hidden_state : h(t-1)'''
        y_hidden_state = tf.expand_dims(hidden_state, axis=1)
        y_hidden_state = self.fc1(y_hidden_state)
        y_enc_out = self.fc2(encoder_output)

        y = tf.keras.backend.tanh(y_enc_out + y_hidden_state)
        attention_score = self.fc3(y)
        attention_weights = tf.keras.backend.softmax(attention_score, axis=1)

        context_vector = tf.multiply(encoder_output, attention_weights)
        context_vector = tf.reduce_sum(context_vector, axis=1)

        return context_vector, attention_weights

In [55]:
class Decoder(tf.keras.Model):
    def __init__(self, hidden_size=1024, max_sequence_len=25, batch_size=batch_size, embedding_dim=100, vocab_size=vocab_size+1):
        super(Decoder, self).__init__()
        self.embedding_dim = embedding_dim
        self.vocab_size = vocab_size
        self.max_sequence_len = max_sequence_len
        self.hidden_size = hidden_size
        self.batch_size = batch_size
    
        self.embedding_layer = Embedding(input_dim=self.vocab_size, output_dim=self.embedding_dim, weights=[embeddings_matrix], trainable=False)
        self.GRU = GRU(units=hidden_size,
                       return_sequences=True, return_state=True, recurrent_initializer='glorot_uniform')
        self.attention = Attention(hidden_size=self.hidden_size)
        self.fc = Dense(units=self.vocab_size)

    def initial_hidden_state(self):
        return tf.zeros(shape=(self.batch_size, self.hidden_size))

    def call(self, x, encoder_output, hidden_state, training=False):
        x = self.embedding_layer(x)
        context_vector, attention_weights = self.attention(
            encoder_output, hidden_state, training=training)
        contect_vector = tf.expand_dims(context_vector, axis=1)
        x = tf.concat([x, contect_vector], axis=-1)
        x, curr_hidden_state = self.GRU(x)
        x = tf.reshape(x, shape=[self.batch_size, -1])
        x = self.fc(x)
        return x, curr_hidden_state, attention_weights

In [56]:
loss_object = tf.losses.SparseCategoricalCrossentropy(from_logits=True)
optimizer = tf.keras.optimizers.Adam(learning_rate=5e-4)
train_accuracy = tf.metrics.SparseCategoricalAccuracy()

def loss_function(y_true, y_pred):
    loss = loss_object(y_true, y_pred)
    mask = 1 - tf.cast(tf.equal(y_true, 0), 'float32')
    return tf.reduce_mean(loss * mask)

In [57]:
def training_step(inputs, responses):    
    with tf.GradientTape() as Tape:
        encoder_init_state = encoder.initial_hidden_state()
        encoder_output, encoder_hidden_state = encoder(inputs, encoder_init_state, training=True)
        decoder_hidden = encoder_hidden_state
        loss = 0
        acc = []
        current_word = tf.expand_dims(responses[:, 0], axis=1)
        for word_idx in range(1, max_sequence_len):
            next_word = responses[:, word_idx]
            logits, decoder_hidden, attention_weights = decoder(current_word, encoder_output, decoder_hidden)
            loss += loss_function(next_word, logits)
            acc.append(train_accuracy(next_word, logits))
            current_word = tf.expand_dims(next_word, axis=1)
    variables = encoder.trainable_variables + decoder.trainable_variables
    gradients = Tape.gradient(loss, variables)
    optimizer.apply_gradients(zip(gradients, variables))
    return loss, tf.reduce_mean(acc)

encoder = Encoder()
decoder = Decoder()

In [58]:
epochs = 7
NUM_SAMPLES = len(X_train)
num_steps = NUM_SAMPLES // batch_size

for epoch in range(1, epochs + 1):
    print(f'Epoch {epoch}/{epochs}')
    ep_loss = []
    ep_acc = []
    progbar = tf.keras.utils.Progbar(target=num_steps, stateful_metrics=[
                                     'curr_loss', 'curr_accuracy'], unit_name='batch')

    for step, example in enumerate(train_dataset):
        inputs = example[0]
        responses = example[1]
        loss, acc = training_step(inputs, responses)
        loss /= responses.shape[1]
        ep_loss.append(loss)
        ep_acc.append(acc)
        progbar.update(
            step + 1, values=[('curr_loss', loss), ('curr_accuracy', acc)])

    print(f'Metrics after epoch {epoch} : Loss => {np.mean(ep_loss):.3f} | Accuracy => {np.mean(ep_acc):.3f}')

Epoch 1/7
1590/1590 [==============================] - 1230s 774ms/batch - curr_loss: 0.4267 - curr_accuracy: 0.8286
Metrics after epoch 1 : Loss => 0.449 | Accuracy => 0.662
Epoch 2/7
1590/1590 [==============================] - 1203s 756ms/batch - curr_loss: 0.3608 - curr_accuracy: 0.8714
Metrics after epoch 2 : Loss => 0.346 | Accuracy => 0.854
Epoch 3/7
1590/1590 [==============================] - 1199s 754ms/batch - curr_loss: 0.3169 - curr_accuracy: 0.8891
Metrics after epoch 3 : Loss => 0.286 | Accuracy => 0.880
Epoch 4/7
1590/1590 [==============================] - 1195s 752ms/batch - curr_loss: 0.2993 - curr_accuracy: 0.9007
Metrics after epoch 4 : Loss => 0.238 | Accuracy => 0.895
Epoch 5/7
1590/1590 [==============================] - 1197s 753ms/batch - curr_loss: 0.2636 - curr_accuracy: 0.9094
Metrics after epoch 5 : Loss => 0.200 | Accuracy => 0.905
Epoch 6/7
1590/1590 [==============================] - 1208s 760ms/batch - curr_loss: 0.2264 - curr_accuracy: 0.9161
Metrics 

In [59]:
def create_response(sentence):
    sentence = preprocess([sentence])
    enc_init = tf.zeros(shape=[1, 1024])
    enc_out, enc_hidden = encoder(sentence, enc_init)
    decoder.batch_size = 1
    tokenizer.index_word[0] = ''
    decoded = []
    att = []
    current_word = tf.expand_dims([word_index['START']], axis=0) 
    decoder_hidden = enc_hidden
    for word_idx in range(1, max_sequence_len):
        logits, decoder_hidden, attention_weights = decoder(current_word, enc_out, decoder_hidden)
        decoded_idx = np.argmax(logits)
        if index_word[decoded_idx] == 'END':
            break
        decoded.append(tokenizer.index_word[decoded_idx])
        att.append(attention_weights.numpy().squeeze())
        current_word = tf.expand_dims([decoded_idx], axis=0)
    return ' '.join(decoded), att

In [63]:
sentences = ['who are you ?',
             'Let us dance',
             'do you miss college?',
             'how are you doing ?', 
             'Are you sad?',
             'what do you want ?',
             'hello',
             'I like food',
             'Miss you',
             'the exam is going to be hard', 
             'i love you', 
             'how are you doing ?', 
             'Help',
             'I am happy',]

for inp_sentence in sentences:
    inp_array = inp_sentence.split()
    inp_len = len(inp_sentence.split())
    trans_sentence, attention_weights = create_response(inp_sentence)
    trans_array = trans_sentence.split()
    trans_len = len(trans_array)
    print('INPUT : ', inp_sentence)
    print('RESPONSE : ', trans_sentence)
    print('-'*30)

INPUT :  who are you ?
RESPONSE :  all right end                     
------------------------------
INPUT :  Let us dance
RESPONSE :  it terrible end                     
------------------------------
INPUT :  do you miss college?
RESPONSE :  be right end                     
------------------------------
INPUT :  how are you doing ?
RESPONSE :  it terrible end                     
------------------------------
INPUT :  Are you sad?
RESPONSE :  sorry end                      
------------------------------
INPUT :  what do you want ?
RESPONSE :  be right end                     
------------------------------
INPUT :  hello
RESPONSE :  end                       
------------------------------
INPUT :  I like food
RESPONSE :  make it end                     
------------------------------
INPUT :  Miss you
RESPONSE :  jason beckmeyer end                     
------------------------------
INPUT :  the exam is going to be hard
RESPONSE :  by all right end                    
--------